In [5]:
"""
Multi-Agent Dynamic Grid World Environment
Created by: Ardianto Wibowo
"""

import numpy as np
import sys
import random

# Add the path to the 'env' folder to sys.path
sys.path.append('env')

from ma_gridworld import Env

def add_noise(data, agent, noise_type="color", env=None, is_noise_enabled=True):
    """
    تضيف نويز للبيانات بناءً على النوع ونسبة النويز.
    """
    noise_level = agent.noise_level  # مستوى نويز خاص بكل وكيل

    # تحقق إذا كانت البيانات None
    if data is None:
        return data

    # نويز الموقع
    if noise_type == "location" and is_noise_enabled and random.random() < noise_level:
        # تحقق إذا كانت البيانات قائمة تحتوي على إحداثيات
        if isinstance(data, list) and len(data) == 2 and all(isinstance(x, int) for x in data):
            grid_width = getattr(env, 'gwidth', 15)  # استخدام قيمة افتراضية إذا لم تكن الخاصية موجودة
            grid_height = getattr(env, 'gheight', 15)
            noise_x = random.choice([1, -1])
            noise_y = random.choice([1, -1])
            new_x = max(0, min(data[0] + noise_x, grid_width - 1))
            new_y = max(0, min(data[1] + noise_y, grid_height - 1))
            return [new_x, new_y]
        else:
            # إذا لم تكن البيانات صالحة لنويز الموقع، قم بإعادتها كما هي
            return data

    if noise_type == "color" and is_noise_enabled and random.random() < noise_level:
        if "target" in data:
            return "empty"
        else:
            return data
    # إذا لم يتم تطبيق نويز، قم بإعادة البيانات كما هي


    return data


class SearchAgent:
    def __init__(self, num_actions, agent_id, num_agents):
        self.num_actions = num_actions
        self.agent_id = agent_id  # تعيين agent_id
        self.memory = []  # خاصية لتخزين البيانات التي يتم التحقق منها
        self.targets_seen = []  # قائمة فارغة لتخزين الأهداف كقواميس
        self.noise_level = round(random.uniform(0, 1), 2)  # مستوى نويز خاص بكل وكيل
        print(f"Agent {self.agent_id}: Initialized with noise level {self.noise_level:.2f}")
        # مستوى الثقة الابتدائي
        self.trust_level = round(random.uniform(0.3, 1.0), 2)
        
        self.true_interaction = {}
        self.false_interaction = {}
        

        # تعيين نفس قيمة الثقة الابتدائية لجميع الوكلاء الآخرين
        self.trust_values = {other_id: self.trust_level for other_id in range(num_agents) if other_id != self.agent_id}

        self.actual_comm_observation = None
        self.reported_comm_observation = None

        print(f"Agent {self.agent_id}: Initialized with trust level {self.trust_level:.2f}")

    def update_trust(self, other_agent_id, interaction_success, use_indirect=False):
        if other_agent_id not in self.true_interaction:
            self.true_interaction[other_agent_id] = 0
            self.false_interaction[other_agent_id] = 0

        if interaction_success:
            self.true_interaction[other_agent_id] = self.true_interaction[other_agent_id] + 1
        else:
            self.false_interaction[other_agent_id] = self.false_interaction[other_agent_id] + 1

        
        if other_agent_id in self.trust_values:
            # الثقة السابقة
            previous_trust = self.trust_values[other_agent_id]

            # نتيجة التفاعل
            interaction_result = 1.0 if interaction_success else 0.0

            # عامل النسيان
            alpha = 0.3  # يمكن ضبطها

            if not use_indirect:
                # الثقة المباشرة فقط
                t_new = (self.true_interaction[other_agent_id] + 1) / (
                            self.true_interaction[other_agent_id] + self.false_interaction[other_agent_id] + 2)
                updated_trust = t_new + alpha * (t_new - previous_trust)
            else:
                # حساب الثقة غير المباشرة
                indirect_trust = 0.0
                total_weight = 0.0

                for intermediary_agent, intermediary_trust in self.trust_values.items():
                    if intermediary_agent != other_agent_id and intermediary_agent in agents[
                        other_agent_id].trust_values:
                        indirect_trust += (
                                intermediary_trust * agents[intermediary_agent].trust_values[other_agent_id]
                        )
                        total_weight += 1.0

                # ضبط الثقة غير المباشرة
                if total_weight > 0:
                    indirect_trust /= total_weight
                else:
                    indirect_trust = 0.01  # قيمة افتراضية صغيرة

                # دمج الثقة المباشرة وغير المباشرة
                updated_trust = (alpha * previous_trust + interaction_result + indirect_trust) / (1 + alpha)

            # ضبط الثقة لتكون بين 0 و 1
            self.trust_values[other_agent_id] = max(0.0, min(1.0, updated_trust))

            # طباعة القيم
            trust_type = "Direct + Indirect" if use_indirect else "Direct"
            print(
                f"Agent {self.agent_id}: Updated trust towards Agent {other_agent_id} ({trust_type}) to {self.trust_values[other_agent_id]:.2f}")

    def normalize_targets(self):
        """
        توحيد شكل البيانات داخل قائمة targets_seen.
        """
        self.targets_seen = [
            {"location": target, "verified": True, "source": "self"} if isinstance(target, list) else target
            for target in self.targets_seen
        ]

    def analyse_sensor_data(self, agent_id, coordinate_observation, sensor_data_observation):

        for i in range(len(sensor_data_observation)):
            for j in range(len(sensor_data_observation[i])):
                data = sensor_data_observation[i][j]
                location = [
                    coordinate_observation[0] + j - len(sensor_data_observation[i]) // 2,
                    coordinate_observation[1] + i - len(sensor_data_observation) // 2
                ]
                if data != None and 'target_' + str(agent_id) in data:
                    if location not in [target["location"] for target in self.targets_seen]:
                        self.targets_seen.append({
                            "location": location,
                            "verified": False,
                            "source": "self"  # أو مصدر آخر حسب الحاجة
                        })
                        print(f"Agent {agent_id}: Added target at {location} to targets_seen")

                # تحديث الذاكرة مع تمرير agent_id
                if data is not None and 'target_' in data:  # التحقق من وجود هدف
                    self.update_memory(location, data, agent_id)  # استدعاء update_memory

                # إزالة الأهداف التي تم جمعها
                if location[0] == coordinate_observation[0] and location[1] == coordinate_observation[1]:
                    if location in self.targets_seen:
                        self.targets_seen.remove(location)

    def analyse_communication(self, comm_observation, agent_id):
        for comm in comm_observation:
            origin_location = comm[0]
            sensor_data_observation = comm[1]
            reported_by = comm[2]  # الوكيل الذي أرسل الرسالة

            print(f"Agent {agent_id}: Received communication from Agent {reported_by} at {origin_location}")

            for i in range(len(sensor_data_observation)):
                for j in range(len(sensor_data_observation[i])):
                    data = sensor_data_observation[i][j]
                    location = [
                        origin_location[0] + j - len(sensor_data_observation[i]) // 2,
                        origin_location[1] + i - len(sensor_data_observation) // 2
                    ]

                    if data is not None and 'target_' in data:
                        if location not in [target["location"] for target in self.targets_seen]:
                            self.targets_seen.append({
                                "location": location,
                                "verified": False,
                                "source": f"agent_{reported_by}"
                            })
                            print(f"Agent {agent_id}: Added target at {location} from Agent {reported_by}")

    def update_memory(self, location, data, agent_id):

        print(f"Agent {agent_id} is updating memory for location {location} with data {data}")
        if location not in [record["location"] for record in self.memory]:
            # add
            self.memory.append({"location": location, "data": data})
            print(f"Agent {agent_id} Updated Memory: {location} -> {data}")

    def select_action(self, coordinate_observation, agent_id):
        print(f"Agent {agent_id}: Current targets seen: {self.targets_seen}")

        # إزالة الأهداف المكررة مع تحويل الموقع إلى tuple
        self.targets_seen = list({tuple(target["location"]): target for target in self.targets_seen}.values())

        if len(self.targets_seen) > 0:
            closest_target = None
            closest_target_distance = float('inf')  # مسافة كبيرة مبدئيًا
            for target in self.targets_seen:
                target_coordinate = target["location"]
                horizontal_distance = target_coordinate[0] - coordinate_observation[0]
                vertical_distance = target_coordinate[1] - coordinate_observation[1]
                distance = abs(horizontal_distance) + abs(vertical_distance)
                print(f"Agent {agent_id}: Target {target_coordinate} at distance {distance}")

                if distance < closest_target_distance:
                    closest_target_distance = distance
                    closest_target = target_coordinate

            if closest_target:
                # التحقق من صلاحية الموقع المستهدف
                grid_width = 15  # عرض الشبكة
                grid_height = 15  # ارتفاع الشبكة
                if not (0 <= closest_target[0] < grid_width and 0 <= closest_target[1] < grid_height):
                    print(f"Invalid target location {closest_target}, skipping target.")
                    closest_target = None

                if closest_target and closest_target_distance == 0:
                    print(f"Agent {agent_id}: Reached target at {closest_target}, removing from targets_seen.")
                    self.targets_seen = [t for t in self.targets_seen if tuple(t["location"]) != tuple(closest_target)]
                    return 0  # Stay

                if closest_target:
                    print(f"Agent {agent_id}: Moving towards target at {closest_target}")
                    horizontal_distance = closest_target[0] - coordinate_observation[0]
                    vertical_distance = closest_target[1] - coordinate_observation[1]
                    if abs(horizontal_distance) >= abs(vertical_distance):
                        return 3 if horizontal_distance < 0 else 4
                    else:
                        return 1 if vertical_distance < 0 else 2
        else:
            print(f"Agent {agent_id}: No valid targets, attempting random action.")
            possible_actions = [1, 2, 3, 4]  # كل الاتجاهات الممكنة
            return np.random.choice(possible_actions)


def get_action(agent_id, observation, num_actions, agents, env):
    """
    تنفيذ خطوة واحدة لكل وكيل، مع تحليل البيانات وتحديث الثقة.
    """
    coordinate_observation = tuple(observation[0])  # Keep observation as (x, y) tuple
    sensor_data_observation = observation[2]
    comm_observation = observation[3]

    print(f"Observation for Agent {agent_id}: {observation}")

    # تحقق من وجود بيانات الاتصال
    if comm_observation:
        for comm in comm_observation:
            origin_location = comm[0]
            data = comm[1]
            reported_by = comm[2]  # الوكيل الذي أرسل البيانات

            # تحليل البيانات المستلمة من وكيل معين
            agents[agent_id].analyse_communication([comm], agent_id)


            # Modify code
            # تحديث الثقة بناءً على الوكيل المصدر للاتصال
            #interaction_success = False  # افتراض التفاعل فشل

            #if data and all(
            #        isinstance(row, list) for row in data):  # تحقق من أن البيانات ليست None وأنها قائمة من القوائم
            #    if any("target_" in cell for row in data for cell in row if cell is not None):
            #        interaction_success = True


            # تحديث الثقة تجاه الوكيل المرسل
            #agents[agent_id].update_trust(reported_by, interaction_success=interaction_success)

            for i in range(len(sensor_data_observation)):
                for j in range(len(sensor_data_observation[i])):
                    data = sensor_data_observation[i][j]
                    location = [
                        coordinate_observation[0] + j - len(sensor_data_observation[i]) // 2,
                        coordinate_observation[1] + i - len(sensor_data_observation) // 2
                    ]
                    for target in agents[agent_id].targets_seen:
                        if location == target["location"] and not target["verified"]:
                            if data != None and 'target_' + str(agent_id) in data:
                                target["verified"] = True
                                if 'agent' in target['source']:
                                    reported_by = int(target['source'].split("_")[1])
                                    print(f"Reach reported target location in {location} report by {reported_by}")
                                    # تحديث الثقة تجاه الوكيل المرسل
                                    agents[agent_id].update_trust(reported_by, interaction_success=True)
                            else:
                                if 'agent' in target['source']:
                                    target["verified"] = True
                                    reported_by = int(target['source'].split("_")[1])
                                    #agents[agent_id].update_trust(reported_by, interaction_success=False)

    else:
        print(f"Agent {agent_id}: No communication data available this step.")

    # تحليل بيانات المستشعر
    agents[agent_id].analyse_sensor_data(agent_id, coordinate_observation, sensor_data_observation)

    # اختيار الإجراء الفيزيائي
    physical_action = agents[agent_id].select_action(coordinate_observation, agent_id)

    if env.is_agent_silent:
        comm_action = []  # Communication action is set to empty if agents are silent
    else:
        # Add noise to communication
        noisy_location = add_noise(coordinate_observation, agents[agent_id], "location", env)
        noisy_data = [
            [add_noise(cell, agents[agent_id], "color", env) for cell in row]
            for row in sensor_data_observation
        ]

        # prevent set noise more thank one time

        comm_action = [noisy_location, noisy_data, agent_id]

        print(f"Agent {agent_id}: Sending noisy communication: Location={noisy_location}, Data={noisy_data}")

    return (physical_action, comm_action)
def run(num_episodes, max_steps_per_episode, agents, num_actions, env):
    import pandas as pd
    import matplotlib.pyplot as plt

    results = []

    for episode in range(num_episodes):
        print(f"Starting episode {episode + 1}")

        # Reset environment
        observations = env.reset()

        # حذف الأهداف القديمة وإنشاء أهداف جديدة
        for target_list in env.target_objs:
            for target in target_list:
                env.canvas.delete(target)

        env.agent_targets = [[] for _ in range(env.num_agents)]
        env.target_objs = [[] for _ in range(env.num_agents)]

        for i in range(env.num_agents):
            for _ in range(env.num_targets_per_agent):
                target_position = env.get_random_target_position()
                env.agent_targets[i].append(target_position)

                target_x, target_y = target_position
                triangle_points = [
                    target_x, target_y - env.UNIT / 4,
                    target_x - env.UNIT / 4, target_y + env.UNIT / 4,
                    target_x + env.UNIT / 4, target_y + env.UNIT / 4
                ]
                target_obj = env.canvas.create_polygon(
                    triangle_points,
                    fill=env.agent_colors[i % len(env.agent_colors)],
                    outline='black'
                )
                env.target_objs[i].append(target_obj)

        print(f"Reinitialized targets for episode {episode + 1}: {env.agent_targets}")

        # Tracking variables
        done = [False] * env.num_agents
        step_count = 0
        agent_steps = {agent_id: 0 for agent_id in range(env.num_agents)}  # Track steps per agent
        agent_goals_achieved = {agent_id: 0 for agent_id in range(env.num_agents)}  # Track goals achieved per agent

        while not all(done) and step_count < max_steps_per_episode:
            actions = []
            for agent_id in range(env.num_agents):
                if not done[agent_id]:  # Only process agents still active
                    observation = observations[agent_id]
                    action = get_action(agent_id, observation, num_actions, agents, env)
                    actions.append(action)
                    agent_steps[agent_id] += 1  # Increment step count
                else:
                    actions.append((0, []))  # No action for agents marked as done

            observations, rewards, done = env.step(actions)

            # Check if goals are achieved and update counters
            for agent_id in range(env.num_agents):
                if rewards[agent_id] > 0:  # Positive reward implies a goal achieved
                    agent_goals_achieved[agent_id] += 1

            step_count += 1
            env.render()

        # Log results for this episode
        for agent_id in range(env.num_agents):
            trust_values = agents[agent_id].trust_values
            trust_columns = {f"Final Trust to Agent {other_id}": round(trust, 3) for other_id, trust in trust_values.items()}

            noise_type = "Color" if getattr(env, 'enable_color_noise', False) else "Location"

            trust_type = "Direct" if getattr(env, 'trust_type', 'Direct') == 'Direct' else "Indirect"

            results.append({
                "Agent ID": agent_id,
                "Noise Level": getattr(agents[agent_id], 'noise_level', 0),
                "Noise Type": noise_type,
                "Trust Type": trust_type,
                "Initial Trust Level": getattr(agents[agent_id], 'trust_level', 0),
                "Steps Taken": agent_steps[agent_id],
                "Goals Achieved": agent_goals_achieved[agent_id],
                "Episode": episode + 1,
                **trust_columns
            })

        print(f"Episode {episode + 1} finished after {step_count} steps.\n")

    # Save results to Excel
    df = pd.DataFrame(results)

    # Create summary data
    summary = df.groupby("Agent ID").agg({
        "Steps Taken": "mean",
        "Goals Achieved": "sum",
        "Noise Level": "first",
        "Noise Type": "first",
        "Trust Type": "first",
        "Initial Trust Level": "first"
    }).reset_index()

    # Adding Final Trust columns to the summary
    final_trust_columns = [col for col in df.columns if col.startswith("Final Trust to Agent")]
    for col in final_trust_columns:
        summary[col] = df.groupby("Agent ID")[col].mean().reset_index(drop=True)

    summary.rename(columns={"Steps Taken": "Average Steps", "Goals Achieved": "Total Goals"}, inplace=True)

    # Save to Excel with two sheets
    with pd.ExcelWriter("experiment_results.xlsx") as writer:
        df.to_excel(writer, index=False, sheet_name="Detailed Results")
        summary.to_excel(writer, index=False, sheet_name="Summary")

    print("Results saved to 'experiment_results.xlsx'.")

    # Plot results: Trust vs Steps Taken
    plt.figure(figsize=(12, 8))

    for agent_id in range(env.num_agents):
        agent_data = df[df["Agent ID"] == agent_id]
        plt.scatter(
            agent_data["Steps Taken"],
            agent_data[[col for col in agent_data.columns if col.startswith("Final Trust to")]].mean(axis=1),
            label=f"Agent {agent_id}"
        )

    plt.xlabel("Steps Taken")
    plt.ylabel("Final Trust Level (Average)")
    plt.title("Final Trust Levels vs Steps Taken (Per Agent)")
    plt.legend()
    plt.grid(True)
    plt.savefig("trust_vs_steps_plot.png")
    plt.show()

    print("Plot saved to 'trust_vs_steps_plot.png'.")


if __name__ == "__main__":

    gsize = 15  # grid size (square)
    gpixels = 30  # grid cell size in pixels

    is_sensor_active = True  # True:  Activate the sensory observation data
    sensory_size = 3  # 'is_sensor_active' must be True. The value must be odd, if event will be converted to one level odd number above

    num_agents = 8  # the number of agents will be run in paralel
    num_obstacles = 0  # the number of obstacles
    is_single_target = False  # True: all agents have a single target, False: each agent has their own target
    num_targets_per_agent = 5  # 'is_single_target' must be true to have an effect

    is_agent_silent = False  # True: communication among agents is allowed

    noise_levels = noise_levels = {agent_id: round(random.uniform(0, 1), 2) for agent_id in range(num_agents)}

    enable_location_noise = True  # تفعيل نويز الموقع
    enable_color_noise = False  # تفعيل نويز اللون
    # نسبة نويز اللون

    num_episodes = 20  # the number of episode will be run
    max_steps_per_episode = 1000  # each episode will be stopped when max_step is reached

    eps_moving_targets = 10  # set this value greater than 'num_episodes' to keep the targets in a stationary position
    eps_moving_obstacles = 10  # set this value greater than 'num_episodes' to keep the obstacles in a stationary position

    render = True  # True: render the animation into the screen (so far, it is still can not be deactivated)

    min_obstacle_distance_from_target = 1  # min grid distance of each obstacles relative to targets
    max_obstacle_distance_from_target = 5  # max grid distance of each obstacles relative to targets
    min_obstacle_distance_from_agents = 1  # min grid distance of each obstacles relative to agents

    reward_normal = -1  # reward value of normal steps
    reward_obstacle = -5  # reward value when hit an obstacle
    reward_target = 50  # reward value when reach the target

    is_totally_random = True  # True: target and obstacles initial as well as movement position is always random on each call, False: only random at the beginning.
    animation_speed = 0.1  # smaller is faster
    is_destroy_environment = True  # True: automatically close the animation after all episodes end.

    # Initialize environment
    env = Env(
        num_agents=num_agents, num_targets_per_agent=num_targets_per_agent, num_obstacles=num_obstacles,
        eps_moving_obstacles=eps_moving_obstacles, eps_moving_targets=eps_moving_targets,
        is_agent_silent=is_agent_silent, is_single_target=is_single_target, sensory_size=sensory_size,
        gpixels=gpixels, gheight=gsize, gwidth=gsize, is_sensor_active=is_sensor_active,
        min_obstacle_distance_from_target=min_obstacle_distance_from_target,
        max_obstacle_distance_from_target=max_obstacle_distance_from_target,
        min_obstacle_distance_from_agents=min_obstacle_distance_from_agents,
        is_totally_random=is_totally_random, animation_speed=animation_speed,
        reward_normal=reward_normal, reward_obstacle=reward_obstacle, reward_target=reward_target
    )

    num_actions = len(env.action_space)

    # Initialize Q-learning agents
    agents = [SearchAgent(num_actions, agent_id, num_agents) for agent_id in range(num_agents)]

    # Run episodes
    run(num_episodes, max_steps_per_episode, agents, num_actions, env)

    if is_destroy_environment:
        env.destroy_environment()


Agent 0: Initialized with noise level 0.91
Agent 0: Initialized with trust level 0.41
Agent 1: Initialized with noise level 0.83
Agent 1: Initialized with trust level 0.92
Agent 2: Initialized with noise level 0.98
Agent 2: Initialized with trust level 0.37
Agent 3: Initialized with noise level 0.13
Agent 3: Initialized with trust level 0.91
Agent 4: Initialized with noise level 0.71
Agent 4: Initialized with trust level 0.30
Agent 5: Initialized with noise level 0.80
Agent 5: Initialized with trust level 0.51
Agent 6: Initialized with noise level 0.81
Agent 6: Initialized with trust level 0.68
Agent 7: Initialized with noise level 0.87
Agent 7: Initialized with trust level 0.91
Starting episode 1
Observation for Agent 0: [[0, 0], False, [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], []]
Agent 0: No communication data available this step.
Agent 0: Current targets seen: []
Agent 0: No valid targets, attempting random action.
Agent 0: Sending noisy communicatio

Step 2:
  Agent 0: Observation: [[1, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(1, 14), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], [None, None, None]], 3], [(7, 0), [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(13, 7), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 5], [(7, 14), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 6], [(0, 6), [[None, 'empty', 'empty'], [None, 'empty', 'empty'], [None, 'agent', 'empty']], 7]]], Action: (4, [(0, 0), [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 0]), Reward: -1, Done: False
  Agent 1: Observation: [[14, 1], False, [['empty', 'agent', None], ['empty', 'empty', None

Step 4:
  Agent 0: Observation: [[3, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'target_0_1']], [[(14, 2), [['empty', 'agent', None], ['empty', 'empty', None], ['empty', 'empty', None]], 1], [(14, 12), [['empty', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 2], [(3, 14), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], [None, None, None]], 3], [(7, 2), [['target_5_2', 'agent', 'empty'], ['empty', 'target_7_1', 'empty'], ['empty', 'empty', 'empty']], 4], [(13, 8), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 5], [(8, 13), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 6], [(2, 6), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 7]]], Action: (4, [(2, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 0]), Reward: -1, Done: False
  Agent 1: Observation: [[14, 3

Step 6:
  Agent 0: Observation: [[4, 1], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['target_6_2', 'empty', 'empty']], [[(14, 4), [['empty', 'agent', None], ['empty', 'empty', None], ['empty', 'empty', None]], 1], [(14, 10), [['empty', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 2], [(5, 14), [['empty', 'empty', 'target_4_0'], ['agent', 'empty', 'empty'], [None, None, None]], 3], [(9, 2), [['empty', 'target_4_1', 'empty'], ['agent', 'empty', 'empty'], ['target_2_2', 'empty', 'empty']], 4], [(12, 7), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['target_0_2', 'agent', 'empty']], 5], [(9, 12), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 6], [(3, 5), [['empty', 'empty', 'empty'], ['agent', 'empty', 'target_5_3'], ['empty', 'empty', 'empty']], 7]]], Action: (2, [(4, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 0]), Reward: 50, Done: False
  Agent

Step 8:
  Agent 0: Observation: [[5, 1], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'target_5_2'], ['empty', 'empty', 'target_7_4']], [[(14, 6), [['empty', 'agent', None], ['empty', 'empty', None], ['empty', 'empty', None]], 1], [(13, 9), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 2], [(6, 13), [['empty', 'empty', 'empty'], ['empty', 'target_4_0', 'empty'], ['empty', 'agent', 'empty']], 3], [(9, 1), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(11, 6), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'target_1_3']], 5], [(9, 12), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 6], [(4, 4), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 7]]], Action: (4, [(4, 1), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 0]), Reward: -1, Don

...

Step 2:
  Agent 0: Observation: [[1, 0], True, [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 14), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(7, 0), [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(14, 7), [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], 5], [(7, 14), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 6], [(0, 7), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 7]]], Action: (4, [(1, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 0]), Reward: 0, Done: True
  Agent 1: Observation: [[14, 0], True, [[None, None, None], ['empty', 'agent', None], ['empty', 'empty

Step 2:
  Agent 0: Observation: [[0, 0], True, [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 14), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(7, 0), [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(14, 7), [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], 5], [(7, 14), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 6], [(0, 7), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 7]]], Action: (1, [(0, 0), [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 0]), Reward: 0, Done: True
  Agent 1: Observation: [[14, 0], True, [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], [

Step 2:
  Agent 0: Observation: [[0, 1], True, [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 14), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(7, 0), [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(14, 7), [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], 5], [(7, 14), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 6], [(0, 7), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 7]]], Action: (2, [(0, 1), [[None, 'agent', 'empty'], [None, 'empty', 'empty'], [None, 'empty', 'empty']], 0]), Reward: 0, Done: True
  Agent 1: Observation: [[14, 1], True, [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 

Step 2:
  Agent 0: Observation: [[1, 0], True, [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 14), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(7, 0), [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(14, 7), [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], 5], [(7, 14), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 6], [(0, 7), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 7]]], Action: (2, [(1, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 0]), Reward: 0, Done: True
  Agent 1: Observation: [[14, 1], True, [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 

Step 2:
  Agent 0: Observation: [[0, 1], True, [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(14, 14), [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 14), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(7, 0), [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'empty', 'empty']], 4], [(14, 7), [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], 5], [(7, 14), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 6], [(0, 7), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'empty']], 7]]], Action: (1, [(0, 1), [[None, 'agent', 'empty'], [None, 'empty', 'empty'], [None, 'empty', 'empty']], 0]), Reward: 0, Done: True
  Agent 1: Observation: [[14, 0], True, [[None, None, None], ['empty', 'agent', None], ['empty', 'empty